In [4]:
from llama_index import Document

doc_example = Document.example()

doc_example

Document(id_='875349f9-3157-4bbe-9917-71b98f9ff188', embedding=None, metadata={'filename': 'README.md', 'category': 'codebase'}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, hash='3183371414f6a23e9a61e11b45ec45f808b148f9973166cfed62226e3505eb05', text='\nContext\nLLMs are a phenomenal piece of technology for knowledge generation and reasoning.\nThey are pre-trained on large amounts of publicly available data.\nHow do we best augment LLMs with our own private data?\nWe need a comprehensive toolkit to help perform this data augmentation for LLMs.\n\nProposed Solution\nThat\'s where LlamaIndex comes in. LlamaIndex is a "data framework" to help\nyou build LLM  apps. It provides the following tools:\n\nOffers data connectors to ingest your existing data sources and data formats\n(APIs, PDFs, docs, SQL, etc.)\nProvides ways to structure your data (indices, graphs) so that this data can be\neasily used with LLMs.\nProvides an advanced retrieval/query inter

# Step 1: Document Loading

1. awesumcare_data

- forms
    - 3 main forms
        - AD
        - EPA
        - Will
- glossory and faq
- blog
- guide for doctor or lawyer
- guide for client
    - docx
    - pdf
    - pptx
    - html

2. Everything on awesumcare.com
    - html

3. Legislation including (English and Chinese):
    Cap. 501 Enduring Powers of Attorney Ordinance
    Cap. 501A Enduring Powers of Attorney (Prescribed Form) Regulation
    Cap. 30 Wills Ordinance
    Cap. 73 Intestates’ Estates Ordinance

    - html
    - csv

Unstructured IO:
https://llamahub.ai/l/file-unstructured
Reranking:
https://twitter.com/llama_index/status/1725189652003610888

In [1]:
from pathlib import Path
from llama_index import download_loader
from llama_index import SimpleDirectoryReader
from custom_io import UnstructuredReader

# UnstructuredReader = download_loader('UnstructuredReader')

# TODO: add filename as metadata, how about category?
dir_reader = SimpleDirectoryReader('./awesumcare_data', file_extractor={
  ".pdf": UnstructuredReader(),
  ".docx": UnstructuredReader(),
  ".pptx": UnstructuredReader(),
}, recursive=True, exclude=["*.png"], file_metadata=None)
documents = dir_reader.load_data()

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_d

In [5]:
from llama_index import Document
from llama_index.embeddings import OpenAIEmbedding
from llama_index.text_splitter import SentenceSplitter
from llama_index.extractors import TitleExtractor
from llama_index.ingestion import IngestionPipeline
from llama_index.vector_stores.qdrant import QdrantVectorStore

import qdrant_client

client = qdrant_client.QdrantClient(location=":memory:")
vector_store = QdrantVectorStore(client=client, collection_name="test_store")

pipeline = IngestionPipeline(
    transformations=[
        SentenceSplitter(),
        TitleExtractor(),
        OpenAIEmbedding(),
    ],
    vector_store=vector_store,
)

# Ingest directly into a vector db
pipeline.run(documents=documents)

# Create your index
from llama_index import VectorStoreIndex

index = VectorStoreIndex.from_vector_store(vector_store)

Extracting titles: 100%|██████████| 5/5 [00:12<00:00,  2.44s/it]


In [33]:
from llama_index import ServiceContext
from llama_index.llms import OpenAI


service_context = ServiceContext.from_defaults(llm=OpenAI("gpt-3.5-turbo-1106"))
vector_store = QdrantVectorStore(client=client, collection_name="test_store")

index = VectorStoreIndex.from_vector_store(vector_store=vector_store, service_context=service_context)
chat_engine = index.as_chat_engine()

In [34]:
chat_engine.chat_repl()

===== Entering Chat REPL =====
Type "exit" to exit.

Assistant: 安心三寶是一個全面的預先護理計劃平台，專為老年人和有需要的人而設，提供一站式解決方案，用於創建與預先護理計劃相關的三個法律文件。

Assistant: 您可以使用「安心三寶網上平台」來建立「平安納」，並按照流程支付$388的費用。



In [30]:
from llama_index.llms import OpenAI
index = VectorStoreIndex.from_documents(documents=documents, service_context=service_context)
chat_engine = index.as_chat_engine()
chat_engine.chat_repl()

===== Entering Chat REPL =====
Type "exit" to exit.

Assistant: 安心三寶是一種預先護理計劃，包括平安紙（遺囑）、持久授權書和預設醫療指示。這些文件旨在幫助個人在失去行為能力或生命末期時，能夠保障自己和家人的權益，並尊重個人的選擇和意願。

Assistant: Hello! How can I assist you today?

Assistant: Is there anything else I can help you with? Feel free to ask if you have any questions or need assistance with anything.



In [17]:
from qdrant_client.http import models
import random
from qdrant import client
res = client.search(
    collection_name="v2",
    search_params=models.SearchParams(hnsw_ef=128, exact=False),
    # create a list of random float with 1536 elements
    query_vector=[random.random() for _ in range(1536)],
    limit=3,
)

In [26]:
res[0].payload

{'file_path': 'awesumcare_data/awesum care doc/for client/高院註冊信.pdf',
 'file_name': '高院註冊信.pdf',
 'file_type': 'application/pdf',
 'file_size': 152943,
 'creation_date': '2023-11-21',
 'last_modified_date': '2023-11-21',
 'last_accessed_date': '2023-11-21',
 '_node_content': '{"id_": "81b71a75-28b6-4347-b62c-c4e0ed736fd2", "embedding": null, "metadata": {"file_path": "awesumcare_data/awesum care doc/for client/\\u9ad8\\u9662\\u8a3b\\u518a\\u4fe1.pdf", "file_name": "\\u9ad8\\u9662\\u8a3b\\u518a\\u4fe1.pdf", "file_type": "application/pdf", "file_size": 152943, "creation_date": "2023-11-21", "last_modified_date": "2023-11-21", "last_accessed_date": "2023-11-21"}, "excluded_embed_metadata_keys": ["file_name", "file_type", "file_size", "creation_date", "last_modified_date", "last_accessed_date"], "excluded_llm_metadata_keys": ["file_name", "file_type", "file_size", "creation_date", "last_modified_date", "last_accessed_date"], "relationships": {"1": {"node_id": "8e99b7fa-b346-4e61-af56-11040

In [23]:
null = None
print(eval(res[0].payload["_node_content"])["text"])

若申請人要求將一項持久授權書註冊時（在授權人精神上無行為能力或正在 變得無行為能力時），必須以書面向高等法院司法常務官提出，並提交以下 文件； a. 申請信。該信述明授權人及申請註冊的受權人或（如適用的話）每一


In [50]:
qdrantClient.get_collections().collections

[]

In [6]:
print(nodes[0])

Node ID: 84c3d74e-1b92-416a-bcd2-d75129a26082
Text: 2023  ADVISOR  https://awesumcare.com  Name  安心三寶  保障未來  無精神行為能力
工作  持久授權書  預設醫療指示  工資、投資、保險  一般退休規劃  傳承  遺囑(平安紙)  人壽保險  退休
被忽略的樂齡及傳承規劃  儲蓄、投資、保險、MPF  什麼是安心三寶？  身故後的遺產安排  第一寶： 平安紙 (遺囑)
失去行為能力時的財產安排  第二寶： 持久授權書  當不能自決時拒絕某些維生治療  第三寶： 預設醫療指示  03  避免親友紛爭  02
保障自己和家人  為什麼需要  安心三寶？  01  尊重自己的選擇  20%  15%  10%  無咁唔好彩？
晚年喪失行為能力機會率非常高  5%  > 25% 會中風...


In [60]:
qdrantClient.get_collection("test_store").vector

CollectionInfo(status=<CollectionStatus.GREEN: 'green'>, optimizer_status=<OptimizersStatusOneOf.OK: 'ok'>, vectors_count=141, indexed_vectors_count=0, points_count=141, segments_count=1, config=CollectionConfig(params=CollectionParams(vectors=VectorParams(size=1536, distance=<Distance.COSINE: 'Cosine'>, hnsw_config=None, quantization_config=None, on_disk=None), shard_number=None, replication_factor=None, write_consistency_factor=None, read_fan_out_factor=None, on_disk_payload=None), hnsw_config=HnswConfig(m=16, ef_construct=100, full_scan_threshold=10000, max_indexing_threads=0, on_disk=None, payload_m=None), optimizer_config=OptimizersConfig(deleted_threshold=0.2, vacuum_min_vector_number=1000, default_segment_number=0, max_segment_size=None, memmap_threshold=None, indexing_threshold=20000, flush_interval_sec=5, max_optimization_threads=1), wal_config=WalConfig(wal_capacity_mb=32, wal_segments_ahead=0), quantization_config=None), payload_schema={})

In [1]:
from app import AwesumCareChatbot
from qdrant import client as qdrantClient
from llama_index.vector_stores.qdrant import QdrantVectorStore

class TestChatbot(AwesumCareChatbot):
    def _setup_index(self):
        vector_store = QdrantVectorStore(client=qdrantClient, collection_name="test_store")
        service_context = ServiceContext.from_defaults(llm=self.llm)

        if "test_store" in [col.name for col in qdrantClient.get_collections().collections] and qdrantClient.get_collection("test_store").vectors_count > 0:
            self.index = VectorStoreIndex.from_vector_store(vector_store, service_context=service_context)
            print("set up index")
            return

        pipeline = IngestionPipeline(
            transformations=[
                SentenceSplitter(),
                TitleExtractor(),
                OpenAIEmbedding(),
            ],
            vector_store=vector_store,
        )
        # Ingest directly into a vector db
        nodes = pipeline.run(documents=self.documents)
        print(nodes[0])
        self.index = VectorStoreIndex.from_vector_store(vector_store, service_context=service_context)
        print("set up index")

chat_bot = TestChatbot(model_name="gpt-4-1106-preview", chunk_size=1024)

/Users/yipwaiming/.pyenv/versions/3.11.6/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


🌍 To view the Phoenix app in your browser, visit http://127.0.0.1:6006/
📺 To view the Phoenix app in a notebook, run `px.active_session().view()`
📖 For more information on how to use Phoenix, check out https://docs.arize.com/phoenix
Setup service context...
Setup vector store...


[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_d

Loaded 23 docs


Extracting titles: 100%|██████████| 5/5 [00:26<00:00,  5.36s/it]


Built index...
Setup chat engine...
Running on local URL:  http://127.0.0.1:7860
[]
[ChatMessage(role=<MessageRole.SYSTEM: 'system'>, content='', additional_kwargs={})]

To create a public link, set `share=True` in `launch()`.


Existing running Phoenix instance detected! Shutting it down and starting a new instance...
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwai

🌍 To view the Phoenix app in your browser, visit http://127.0.0.1:6006/
📺 To view the Phoenix app in a notebook, run `px.active_session().view()`
📖 For more information on how to use Phoenix, check out https://docs.arize.com/phoenix
Setup service context...
Setup vector store...
Loaded 23 docs


NameError: name 'ServiceContext' is not defined

In [1]:
import gradio as gr

def vote(data: gr.LikeData):
    if data.liked:
        gr.Info("You up-voted this response: " + data.value)
    else:
        gr.Info("You down-voted this response: " + data.value)


chatbot = gr.Chatbot()

with gr.Blocks() as demo:
    gr.Markdown("# Awesum Care demo")

    with gr.Tab("With awesum care data prepared"):
        gr.ChatInterface(
            chat_bot.stream_chat,
            chatbot=chatbot,
            examples=chat_bot.CHAT_EXAMPLES,
        )
        chatbot.like(vote, None, None)

demo.queue()
demo.launch()

/Users/yipwaiming/.pyenv/versions/3.11.6/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


NameError: name 'chat_bot' is not defined

In [ ]:
text_list = ["123", "234", ...]
documents = [Document(text=t) for t in text_list]

for text in text_list:
    document = Document(
        text="text",
        metadata={"filename": "<doc_file_name>", "category": "<category>"},
    )
    documents.append(document)

In [1]:
from app import AwesumCareChatbot

awesum_chatbot = AwesumCareChatbot("gpt-3.5-turbo-1106", 
                                   chunk_size=2048,
                                   vdb_collection_name="v0")

🌍 To view the Phoenix app in your browser, visit http://127.0.0.1:6006/
📺 To view the Phoenix app in a notebook, run `px.active_session().view()`
📖 For more information on how to use Phoenix, check out https://docs.arize.com/phoenix
Setup service context...
Setup vector store...


[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_d

Loaded 23 docs
Built index...
Setup chat engine...
Running on local URL:  http://127.0.0.1:7860

To create a public link, set `share=True` in `launch()`.


Existing running Phoenix instance detected! Shutting it down and starting a new instance...
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/yipwaiming/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/yipwai

🌍 To view the Phoenix app in your browser, visit http://127.0.0.1:6006/
📺 To view the Phoenix app in a notebook, run `px.active_session().view()`
📖 For more information on how to use Phoenix, check out https://docs.arize.com/phoenix
Setup service context...
Setup vector store...
Loaded 23 docs
Built index...
Setup chat engine...


In [2]:
awesum_chatbot.chat_engine.chat_repl()

===== Entering Chat REPL =====
Type "exit" to exit.

Assistant: Hello! How can I assist you today?

[]
[ChatMessage(role=<MessageRole.SYSTEM: 'system'>, content='', additional_kwargs={})]
Assistant: 安心三寶是指在面對失去行為能力或病情惡化時，能夠保障個人權益和財務安排的重要文件。它包括三份法律文件：平安紙（遺囑）、持久授權書和預設醫療指示。平安紙用於處理遺產安排和遺願，持久授權書則允許他人代表你處理財務事務，而預設醫療指示則是在無法自主決定時，拒絕某些維生治療的指示。這三份文件能夠保障你的權益，避免親友紛爭，並尊重你的選擇。希望這能幫到你！

Assistant: 如果你有任何其他問題，請隨時告訴我！



[['hi', 'Hello! How can I assist you today?']]
[ChatMessage(role=<MessageRole.SYSTEM: 'system'>, content='', additional_kwargs={}), ChatMessage(role=<MessageRole.USER: 'user'>, content='hi', additional_kwargs={}), ChatMessage(role=<MessageRole.ASSISTANT: 'assistant'>, content='Hello! How can I assist you today?', additional_kwargs={})]


Traceback (most recent call last):
  File "/Users/yipwaiming/.pyenv/versions/3.11.6/lib/python3.11/site-packages/gradio/queueing.py", line 456, in call_prediction
    output = await route_utils.call_process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/yipwaiming/.pyenv/versions/3.11.6/lib/python3.11/site-packages/gradio/route_utils.py", line 232, in call_process_api
    output = await app.get_blocks().process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/yipwaiming/.pyenv/versions/3.11.6/lib/python3.11/site-packages/gradio/blocks.py", line 1522, in process_api
    result = await self.call_function(
             ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/yipwaiming/.pyenv/versions/3.11.6/lib/python3.11/site-packages/gradio/blocks.py", line 1156, in call_function
    prediction = await utils.async_iteration(iterator)
                 ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/yipwaiming/.pyenv/versions/3.11.6/lib/python3.11/site-pack

In [3]:
from docx import Document

def read_docx(file_path):
    doc = Document(file_path)
    full_text = []
    for i, para in enumerate(doc.paragraphs):
        print(f"{i}- {para.text}")
        # full_text.append(para.text)
    # return '\n'.join(full_text)

text = read_docx('/Users/yipwaiming/repos/awesum_care_demo/awesumcare_data/awesumcarematerials/AD_Glossary and FAQ (Chinese).docx')
# print(text)


0- 詞彙表
1- 
2- 預設醫療指示
3- 一份由精神有行為能力做出決定的人作出的指示，表明他/她未來若失去精神上做決定的能力時想拒絕接受的治療。
4- 
5- 維持生命治療
6- 維持生命治療是指任何能夠延遲病人死亡的治療，包括心肺復甦術、人工輔助呼吸、血液製品、心臟起搏器、血管增壓藥、針對特別病況的專門治療(例如化學治療或透析治療)、對可能致命的感染提供抗生素，以及人工營養及流體餵養。
7- 
8- 人工營養及流體餵養
9- 人工營養及流體餵養指不經口腔而經喉管或靜脈等方式向某人供給食物或液體。
10- 
11- 基本護理和紓緩治療
12- 紓緩治療及晚期照顧是用以協助患有持續惡化及不可逆轉疾病的病人和其家人／照顧者的方法，以改善其生活質素。
13- 
14- 心肺復甦術
15- 心肺復甦術一種救助心搏驟停病患的急救措施，通過人工呼吸，保持腦功能直到自然呼吸和血液循環恢復。
16- 
17- 病情到了末期
18- 定義為患有嚴重、持續惡化及不可逆轉的疾病，而且對針對病源的治療毫無反應，預期壽命短暫，僅得數日、數星期或數月的生命。提供維持生命治療只能延遲死亡時間。
19- 
20- 持續植物人狀況或不可逆轉昏迷的狀況
21- 持續植物人是一種因腦部受到大幅度及不可逆轉的破壞， 導致病人不大可能脫離植物人狀況，是一種慢性或長期的狀況。而不可逆轉的昏迷則指病人完全失去意識和知覺的狀況。植物人狀況的病人可能已從昏迷狀況醒過來，只是未能恢復意識。
22- 
23- 其他晚期不可逆轉的生存受限疾病
24- 意思是指患有嚴重、持續惡化及不可逆轉的疾病，但不屬於「病情到了末期」或「持續植物人狀況和不可逆轉昏迷的狀況」，不過病情已到了晚期，而病人的生存已經受限的狀況。
25- 
26- 
27- 常見問題
28- 
29- 預設醫療指示有什麽用處？
30- 
31- 計劃治療 - 預設醫療指示能在病人失去精神上的行為能力，無法表達自己的意願以前，訂立病人對自己的治療的安排。
32- 自決 –透過讓病人拒絕接受維持生命治療，以減低其承受的苦楚和維護其尊嚴，從而保障病人對自己生命的控制權。
33- 安撫家人和朋友 – 讓家人和朋友預先知道病人的決定，以免他們要為他們的摯愛作出關乎生死的艱難的決定。
34- 協助醫護人員 – 醫護人員有責任需要為病人提供維持生命治療，即使該治療不能

In [4]:
def parse_knowledge_units(file_path):

    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    knowledge_units = []
    current_unit = ""

    for line in lines:
        if line.strip() and line[0].isdigit() and '.' in line:
            if current_unit:
                knowledge_units.append(current_unit.strip())
                current_unit = ""
            current_unit += line
        else:
            current_unit += line

    if current_unit:
        knowledge_units.append(current_unit.strip())

    return knowledge_units

# Example usage
knowledge_units = parse_knowledge_units('/Users/yipwaiming/repos/awesum_care_demo/awesumcare_data/awesumcarematerials/AD in Eng version (2023).md')

# for unit in knowledge_units:
    # print(unit)
    # print('--------------------------------')

knowledge_units

['+-----------------------------------------------------------------------+\n| > **ADVANCE DIRECTIVE^1^**                                            |\n+=======================================================================+\n| > **[Section I : Personal details of the maker of this advance        |\n| > directive]{.underline}**                                            |\n| >                                                                     |\n| > **Name :** *(please use capital letters)*                           |\n| >                                                                     |\n| > **Identity Document No.:**                                          |\n| >                                                                     |\n| > **Sex : Male / Female**                                             |\n| >                                                                     |\n| > **Date of Birth : / /**                                             |\n| >                    

In [6]:
def read_markdown(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        for i in file.readlines():
            print(i.strip())

markdown_text = read_markdown('test01.md')
print(markdown_text)

**詞彙表**

1.  **預設醫療指示 (advance medical directive/AMD)**

> 指某人訂立的、載有一項或多於一項內容如下的指令的文書：如該人無精神能力就維持生命治療作決定，而該指令的指明先決條件亦獲符合，則不得對該人施以該指令指明的維持生命治療。

2.  **維持生命治療 (life-sustaining treatment)**

> 維持生命治療是指對維持某人的生命屬必要的醫治，但不包括基本護理及紓緩治療。就處於持續性植物人狀態的人而言，維持生命治療的一個例子，是透過喉管或導致管，向該人供給飲食（即人工供給營養及液體）。

3.  **人工營養及流體餵養(artificial and hydration)**

> 人工營養及流體餵養指不經口腔而經喉管或靜脈等方式向某人供給食物或液體。

4.  **基本護理 (basic care)**

> 指向病人提供並對維持該病人舒適屬必要的個人護理；

基本護理的例子如下-------

(a) 向病人提供讓其經口腔進食食物和飲用飲料；

(b) 協助病人經口腔進食食物和飲用飲料；

(c) 維持病人個人衛生的措施；

(d) 減輕病人痛楚的措施。

```{=html}
<!-- -->
```
5.  **紓緩治療(palliative care)**

> 指向病人提供其目的是透過避免和減輕病人在身體、心理、社交或心靈上所受的痛苦或困擾，改善該病人的生活質素及提供該項治療或支援的方法，是適時評估和減輕該痛苦或困擾。

6.  **待援者 (person-in-arrest)**

指處於心肺停頓狀況的人。

7.  **心肺復甦術（cardiopulmonary resuscitation/CPR）**

> 心肺復甦術是對待援者施行的緊急維持生命治療，其目的是恢復或維持該待援者的重要器官的血液循環及氧氣供應；
>
> 心肺復甦術的程序的例子如下 ---
>
> （a) 心臟按壓；
>
> \(b\) 人工呼吸；
>
> (c)電擊除顫。

8.  **病情到了末期 (terminally ill)**

> 定義為患有嚴重、持續惡化及不可逆轉的疾病，而且對上述病情沒有反應，預期壽命短暫至以數日、數週或數月的計算。提供維持生命治療只能延遲死亡時間。

9.  **持續植物人

In [9]:
import os
import glob
import csv

directory_path = '/Users/yipwaiming/repos/awesum_care_demo/awesumcare_data/awesumcare_manual_data'
csv_files = glob.glob(os.path.join(directory_path, 'new things for AI to learn - *.csv'))

total_rows = 0
row_number = 31

for csv_file in csv_files:
    with open(csv_file, 'r', encoding='utf-8') as file:
        reader = csv.reader(file)
        next(reader)  # Skip the first row
        for row in reader:
            if len(row) >= 2:
                print(f"{row_number}. {row[0]}\n{row[1]}\n")
                # print("\n")
                total_rows += 1
                row_number += 1

print(f"Total rows: {total_rows}")


31. 遺產承辦是什麼？
遺產的種類：親屬去世後，可能留下遺產（如銀行存款、公司股票、物業等）。申請遺產承辦書：無論有無遺囑，需先取得高等法院的遺產承辦書。由於過程繁複，建議安排律師協助處理。

32. 在有遺囑情況下，怎樣辦理遺產承辦？
遺囑執行人的資格：遺囑執行人有資格申請遺囑認證書。 遺囑執行人的職責：若遺囑執行人不履行任務或已去世，其餘遺產受益人可申請遺產管理書（附有遺囑）。遺產分配：獲得剩餘遺產需扣除所有受益人分得的遺產、死者債務及相關費用。

33. 在無遺囑情況下，怎樣辦理遺產承辦？
需依照無遺囑繼承法律申請遺產管理書。

34. 無遺囑遺產承辦申請人優先次序 是什麼？
根據《無爭議遺囑認證規則》（香港法例第10A章）第21條，申請人的優先次序如下：1. 尚存的配偶 2.死者的子女 3.死者的父母 4.死者的兄弟姊妹（如已身故，其後裔）遺產管理人數量：最多可有四個遺產管理人，需證明親屬關係。有爭議的情況：有爭議時，可向高等法院申請決定遺產管理人。

35. 從法律角度看何伯財產爭議
從法律角度看何伯財產爭議 事件簡介 近日，一宗引起廣泛關注的案件在社交媒體上掀起熱議：76歲的何伯結識了一位年輕30歲的內地女子，兩人迅速墜入愛河並閃電結婚，卻遭到何伯五名子女的強烈反對，懷疑新婚妻子意圖騙取父親財產。隨後，何伯在準備提取定期戶口中100萬港元進行投資時，發現450萬港元已被小女兒提走，引發網民激烈討論。這不僅成為大家茶餘飯後的熱門話題，還引發了關於老年人財產安全的廣泛討論。 法律角度上的議題 聯名銀行戶口 – 450萬港元女兒提取，是否饋贈？ 何伯與其小女兒共同持有的一個聯名銀行戶口存款450萬港元，存款被小女兒提取。聯名戶口的持有人共同享有使用戶口資金的權利，而提款是否需要所有持有人簽名則視乎開立戶口時選擇了「單簽」還是「雙簽」。新何太聲稱這些資金並非繼承，只是管理用途。然而，這筆資金的提取是否構成饋贈，或是否應該根據「生存者取得權」(長命契)來處理，仍有待法庭進一步釐清。這也反映聯名戶口並不能取代訂立平安紙和持久授權書。欲知更多聯名戶口事宜，請看【聯名戶口提款】在沒有遺囑認證的情況下我可以從與死者的聯名戶口中提款嗎？這篇網誌。 定期存款 – 是否應考慮購買年金以確保穩定收入？ 何伯原本依靠定期存款過活，但這種方式存在一次性被提取的風險。相比之下，購買年

In [9]:
import re

def parse_knowledge_units(file_path):
    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    knowledge_units = []
    current_unit = ""
    unit_start_pattern = re.compile(r'^\d+\.\s')
    for line in lines:
        stripped_line = line.strip()
        if unit_start_pattern.match(stripped_line):
            if current_unit:
                knowledge_units.append(current_unit.strip())
                current_unit = ""
            current_unit += line
        else:
            current_unit += line

    if current_unit:
        knowledge_units.append(current_unit.strip())
    # for line in lines:
    #     if line.strip() and line[0].isdigit() and '.' in line:
    #         if current_unit:
    #             knowledge_units.append(current_unit.strip())
    #             current_unit = ""
    #         current_unit += line
    #     else:
    #         current_unit += line

    # if current_unit:
    #     knowledge_units.append(current_unit.strip())

    return knowledge_units

knowledge_units_list = parse_knowledge_units("/Users/yipwaiming/repos/awesum_care_demo/awesumcare_data/awesumcare_manual_data/常見問題 - 安心三寶.md")

for unit in knowledge_units_list:
    import tiktoken
    def count_tokens(text, model_name="text-embedding-ada-002"):
        encoding = tiktoken.encoding_for_model(model_name)
        tokens = encoding.encode(text)
        return len(tokens)

    def truncate_text(text, max_tokens=8192, model_name="text-embedding-ada-002"):
        encoding = tiktoken.encoding_for_model(model_name)
        tokens = encoding.encode(text)
        if len(tokens) > max_tokens:
            tokens = tokens[:max_tokens]
        return encoding.decode(tokens)

    token_count = count_tokens(unit)
    print(token_count)
    if token_count > 8192:
        print("hi")
        break
        unit = truncate_text(unit, max_tokens=8192)
    print(f"{unit}\n\n")


109
1.  **甚麼是安⼼三寶？**

> 安⼼三寶是⼀個簡單的網上平台 /
> ⼿機應⽤程式，⽅便⼤家⾃⼰訂立平安三寶(尤其是長者以及以及其他有需要⼈⼠)。


237
2.  **「安⼼三寶」 / 「平安三寶」是指哪「三寶」？**

> 「安⼼三寶」 / 「平安三寶」-
> 是指三份具不同功能的法律⽂件，為⾃⼰或家⼈在失去⾏為能⼒或過世時提供保障：
>
> 第⼀寶：平安紙 ( 遺囑 ) -- ⾝故後的遺產安排。
>
> 第⼆寶：持久授權書 -- 失去⾏為能⼒時作出財產安排。
>
> 第三寶：預設醫療指⽰ -- 失去⾏為能⼒時對⾃⾝的醫療安排。


266
3.  **為甚麼需要「安⼼三寶」 / 「平安三寶」？**

> ⼈⼝老化的問題⽇趨嚴重，再加上新冠肺炎肆虐，⼤家需要為⾃⼰失去⾏為能⼒或離世作好準備。
>
> ⽽安⼼三寶所提供的三份⽂件可以在閣下失去⾏為能⼒或⾝故前對⾃⼰的財務及醫療作出安排，令到⾃⼰和家⼈更加「安⼼」。
>
> 有關詳情，⼤家可以參考我們YouTube頻道「為甚麼要平安三寶」的短片：
>
> <https://youtu.be/Zs6F30U44ng>


166
4.  **如何製作安⼼三寶？**

> ⼤家可以到我們的YouTube頻道觀看訂立平安三寶的三條短片。 影片教學

[如何製作平安紙?](https://www.youtube.com/watch?v=l29cJGtnKrk)

> [如何製作持久授權書?](https://www.youtube.com/watch?v=M0V7zFhyhT8)
>
> [如何製作預設醫療指⽰?](https://www.youtube.com/watch?v=rcbwJcH5SME)


733
6.  **通過安⼼三寶製作的⽂件有法律效⼒嗎？**

> 平安紙 ( 遺囑 )

香港法例沒有對平安紙的樣式有特定要求，也不一定要找律師製作。
**「安⼼三寶」**
⽤⼾可以通過安心三寶正確填寫內容，下載並列印⽂件。在兩名非遺產受益的成年人面前簽署和⾒證後，⽂件便可以擁有法律效⼒。兩名見證人不一定需要是律師或醫生
，如果立囑人年紀老邁，或對其精神行為能力有懷疑，最好找個醫生見證。

> 持久授權書
>
> 持久授權書需要依循香港法例的樣式要求 製作。 **「安⼼三寶」**
> ⽤⼾需要正確填寫